In [1]:
import sys
from pathlib import Path

# Add parent directory to sys.path
parent_dir = Path().resolve().parent  # current folder's parent
sys.path.append(str(parent_dir))

import geopandas as gpd 
from shapely import wkt
import pandas as pd
import numpy as np
import isochrones 
import population 
import h3_utils
import geoutils
import api_keys
import quality_utils
import osm
import osmnx as ox
import graph_processing
import geoprocessing 
import map_utils

import os
import re

In [2]:
aoi = geoutils.get_city_geometry("Ghana")
countrycode = "GH"

reference_distance = 1000
max_distance = 10000
elasticity = 0.3
min_edge_length = reference_distance/10
h3_resolution = 8

results_path = "../data"
data_path = "../data/Virtue-Foundation-Ghana-enriched.csv"
geocoded_path = results_path + "/Virtue-Foundation-Ghana-enriched_geocoded.csv"
aoi_path = results_path + "/aoi.gpkg"

In [3]:
aoi.to_file(aoi_path)

In [4]:
!python geocode.py {countrycode} {data_path} {geocoded_path} {aoi_path}
data = pd.read_csv(geocoded_path)
data["geometry"] = data["geometry"].apply(lambda x: wkt.loads(x))
data = gpd.GeoDataFrame(data, geometry="geometry", crs=4326)
data

Data is already complete


source_url  \
0               https://www.linkedin.com/company/waaf/   
1    https://www.ghanabusinessweb.com/accra-adabrak...   
2    https://www.ghanayello.com/company/54942/2BN_M...   
3    https://www.ghanabusinessweb.com/accra-cantonm...   
4             https://www.facebook.com/792273274467144   
..                                                 ...   
792           https://www.facebook.com/359342804713804   
793           https://www.facebook.com/253792632171658   
794  https://www.ghanayello.com/company/52344/Zabzu...   
795           https://www.facebook.com/373009253073815   
796          https://www.facebook.com/1171486939536895   

                                                  name  pk_unique_id  \
0              Behind the Chief's Palace Abesim, Ghana             1   
1                                1st Foundation Clinic             2   
2                                2BN Military Hospital             3   
3                                 37 Military Hospital             4   
4                     3E Medical Center - Accra, Ghana             5   
..                                                 ...           ...   
792                            Yendi District Hospital           793   
793                              You Hao Dental Clinic           794   
794                   Zabzugu Tatale District Hospital           795   
795                          Zebilla District Hospital           796   
796  Zoe Royal Hospital - Fertility Centre, Accra, ...           797   

                     mongo DB  \
0    62aa51490990af00169ab9ed   
1                         NaN   
2    627575867a35920016fe144c   
3    5ea3146e994ecc38cda4ec80   
4                         NaN   
..                        ...   
792  5ea3146e994ecc38cda4eceb   
793                       NaN   
794  62b0e42aa7516a001629846e   
795  5ea3146e994ecc38cda4ecf3   
796                       NaN   

                                           specialties  \
0    ['infectiousDiseases', 'hospiceAndPalliativeIn...   
1                                 ['internalMedicine']   
2    ['internalMedicine', 'dentistry', 'emergencyMe...   
3                                 ['internalMedicine']   
4                                 ['internalMedicine']   
..                                                 ...   
792                               ['internalMedicine']   
793                                      ['dentistry']   
794                               ['internalMedicine']   
795    ['internalMedicine', 'gynecologyAndObstetrics']   
796  ['reproductiveEndocrinologyAndInfertility', 'i...   

                                             procedure equipment  \
0    ['PMTCT services', 'Hospice / home-based care'...        []   
1                                                   []        []   
2                                                   []        []   
3                                                   []        []   
4                                                   []        []   
..                                                 ...       ...   
792                                                 []        []   
793  ['Provides dental fillings', 'Provides dentures']        []   
794                                                 []        []   
795                                                 []        []   
796                                                 []        []   

                                            capability organization_type  \
0    ['Has a location at 109/No 1 Bekwai Rd (Near M...          facility   
1    ['Located in Dansoman, Accra, Ghana, opposite ...          facility   
2                                                   []          facility   
3       ['Located at Liberation Rd. 37, Accra, Ghana']          facility   
4    ['Located in Accra, Ghana', 'Always open', 'Ph...          facility   
..                                                 ...               ...   
792  ['Located in Yendi, Ghana', 'Opera

In [5]:
data['stars'] = 3

In [6]:
pop_h3 = geoprocessing.get_pop_h3(
    aoi,results_path
)

In [7]:
iso_df, iso_df_h3, iso_df_pop = geoprocessing.coverage(
    data,
    elasticity, 
    reference_distance, 
    max_distance,
    pop_h3,
    h3_resolution
)

100%|██████████| 7/7 [00:00<00:00, 93.67it/s]
/home/miguel/Documents/Proyectos/HackanationMIT/Health-Connect/geoprocessing/geoprocessing.py:265: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  iso_df_h3_pop.geometry = iso_df_h3_pop.geometry.centroid


In [8]:
poi = aoi.copy()
poi.geometry = poi.geometry.centroid

/tmp/ipykernel_73720/1219760571.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  poi.geometry = poi.geometry.centroid


In [11]:
data_dist = geoprocessing.poi_distance_quality(    
    data,
    poi,  
    elasticity, 
    reference_distance, 
    max_distance*100
)
data_dist

source_url  \
0               https://www.linkedin.com/company/waaf/   
1    https://www.ghanabusinessweb.com/accra-adabrak...   
2    https://www.ghanayello.com/company/54942/2BN_M...   
3    https://www.ghanabusinessweb.com/accra-cantonm...   
4             https://www.facebook.com/792273274467144   
..                                                 ...   
792           https://www.facebook.com/359342804713804   
793           https://www.facebook.com/253792632171658   
794  https://www.ghanayello.com/company/52344/Zabzu...   
795           https://www.facebook.com/373009253073815   
796          https://www.facebook.com/1171486939536895   

                                                  name  pk_unique_id  \
0              Behind the Chief's Palace Abesim, Ghana             1   
1                                1st Foundation Clinic             2   
2                                2BN Military Hospital             3   
3                                 37 Military Hospital             4   
4                     3E Medical Center - Accra, Ghana             5   
..                                                 ...           ...   
792                            Yendi District Hospital           793   
793                              You Hao Dental Clinic           794   
794                   Zabzugu Tatale District Hospital           795   
795                          Zebilla District Hospital           796   
796  Zoe Royal Hospital - Fertility Centre, Accra, ...           797   

                     mongo DB  \
0    62aa51490990af00169ab9ed   
1                         NaN   
2    627575867a35920016fe144c   
3    5ea3146e994ecc38cda4ec80   
4                         NaN   
..                        ...   
792  5ea3146e994ecc38cda4eceb   
793                       NaN   
794  62b0e42aa7516a001629846e   
795  5ea3146e994ecc38cda4ecf3   
796                       NaN   

                                           specialties  \
0    ['infectiousDiseases', 'hospiceAndPalliativeIn...   
1                                 ['internalMedicine']   
2    ['internalMedicine', 'dentistry', 'emergencyMe...   
3                                 ['internalMedicine']   
4                                 ['internalMedicine']   
..                                                 ...   
792                               ['internalMedicine']   
793                                      ['dentistry']   
794                               ['internalMedicine']   
795    ['internalMedicine', 'gynecologyAndObstetrics']   
796  ['reproductiveEndocrinologyAndInfertility', 'i...   

                                             procedure equipment  \
0    ['PMTCT services', 'Hospice / home-based care'...        []   
1                                                   []        []   
2                                                   []        []   
3                                                   []        []   
4                                                   []        []   
..                                                 ...       ...   
792                                                 []        []   
793  ['Provides dental fillings', 'Provides dentures']        []   
794                                                 []        []   
795                                                 []        []   
796                                                 []        []   

                                            capability organization_type  \
0    ['Has a location at 109/No 1 Bekwai Rd (Near M...          facility   
1    ['Located in Dansoman, Accra, Ghana, opposite ...          facility   
2                                                   []          facility   
3       ['Located at Liberation Rd. 37, Accra, Ghana']          facility   
4    ['Located in Accra, Ghana', 'Always open', 'Ph...          facility   
..                                                 ...               ...   
792  ['Located in Yendi, Ghana', 'Opera

In [ ]:
# for all the maps select at the vars you put in pois and gdfs the columns you really want to plot including always 'geometry' and 'h3_cell' and column and poi_column if available

In [ ]:
m=map_utils.general_map(
    aoi=aoi,
    pois=data,
    gdfs=iso_df,
    poi_column="stars",
    poi_cmap="Blues",
    poi_vmin=1,
    poi_vmax=5,
    column="accessibility",
    cmap="RdYlGn",
    vmin=0.1,
    vmax=1
)
#m.save("map.html")
m

In [ ]:
m=map_utils.general_map(
    aoi=aoi,
    pois=data,
    gdfs=iso_df_h3,
    poi_column="stars",
    poi_cmap="Blues",
    poi_vmin=1,
    poi_vmax=5,
    column="accessibility",
    cmap="RdYlGn",
    vmin=0.1,
    vmax=1
)
#m.save("map.html")
m

In [ ]:
m=map_utils.general_map(
    aoi=aoi,
    pois=data,
    gdfs=iso_df_pop,
    poi_column="stars",
    poi_cmap="Blues",
    poi_vmin=1,
    poi_vmax=5,
    column="accessibility",
    cmap="RdYlGn",
    size_column="population",
    vmin=0.1,
    vmax=1
)
#m.save("map.html")
m